In [13]:
import pandas as pd
import numpy as np
import torch
import torch.nn as nn
from torch.utils.data import TensorDataset, DataLoader
from torch import Tensor
import torch.nn.functional as F
from torch.optim.lr_scheduler import MultiStepLR
from torch.utils.tensorboard import SummaryWriter

In [14]:
# Device configuration
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')
device

device(type='cuda', index=0)

In [15]:
# Convolutional neural network (two convolutional layers)
class GRU_AT(nn.Module):
    def __init__(self, num_classes=4):
        super(GRU_AT, self).__init__()
           
        self.d1 = nn.Dropout(p=0.25)      
        self.bn1 = nn.BatchNorm1d(64)
        self.gru = nn.GRU(64,256,dropout=0.25)
        self.fc1 = nn.Linear(256, 64)
        self.fc2 = nn.Linear(64, num_classes)
        #attention parameter
        self.u = torch.randn(8,device=device,requires_grad=True)
        self.fc_attention = nn.Linear(256, 8)
        self.ac_attention = nn.Softmax(dim=1)
        
    def forward(self, x):    
       
        #b,64,64
        x, _= self.gru(x)
        #b,64,256
        temp1 = self.fc_attention(x)
        temp1 = F.tanh(temp1)
        #b,64,8
        alpha = torch.tensordot(temp1,self.u,1)
        alpha = self.ac_attention(alpha)
        #b,64 = b,64,8 8
        alpha = alpha.reshape(-1,64,1)
        #b,64,1
        x = torch.mul(x,alpha)
        #b,64,256 * b,64,1 = b,64,256
        x = torch.sum(x,dim=1)
        #b,64,256 -> b,,256
        x = self.fc1(x)
        x = self.bn1(x)
        x = F.softplus(x)
        x = self.d1(x)
        x = self.fc2(x)

        return x

In [16]:
test = GRU_AT(4).to(device)
a = torch.randn(10,64,64)
a = a.to(device)
out = test(a)
out.shape

C:\Users\murray\anaconda3\envs\pytorchEEG\lib\site-packages\torch\nn\functional.py:1795: UserWarning: nn.functional.tanh is deprecated. Use torch.tanh instead.
  warnings.warn("nn.functional.tanh is deprecated. Use torch.tanh instead.")


torch.Size([10, 4])

In [17]:
writer = SummaryWriter()

In [18]:
train_set = pd.read_csv("data/final_format/train_set.csv",header=None).to_numpy()
train_label = pd.read_csv("data/final_format/train_label.csv",header=None).to_numpy()
test_set = pd.read_csv("data/final_format/test_set.csv",header=None).to_numpy()
test_label = pd.read_csv("data/final_format/test_label.csv",header=None).to_numpy()

In [19]:
#delet first row data
train_set = train_set[1:]
train_label = train_label[1:]
test_set = test_set[1:]
test_label = test_label[1:]
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 4096) (14392, 1) (3598, 4096) (3598, 1)


In [20]:
train_label = train_label.reshape(-1)
test_label = test_label.reshape(-1)
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 4096) (14392,) (3598, 4096) (3598,)


In [21]:
#transpose to set data in time sequence
train_set = train_set.reshape(-1,64,64)
train_set = np.transpose(train_set,[0,2,1])
test_set = test_set.reshape(-1,64,64)
test_set = np.transpose(test_set,[0,2,1])
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 64, 64) (14392,) (3598, 64, 64) (3598,)


In [22]:
# Hyper parameters
num_epochs = 300
num_classes = 4
batch_size = 64
learning_rate = 1e-3

In [23]:
train_set_tensor = Tensor(train_set) 
train_label_tensor = Tensor(train_label).type(torch.LongTensor)

train_dataset = TensorDataset(train_set_tensor,train_label_tensor) 
train_loader = DataLoader(train_dataset, batch_size=batch_size) 

test_set_tensor = Tensor(test_set) 
test_label_tensor = Tensor(test_label).type(torch.LongTensor)

test_dataset = TensorDataset(test_set_tensor,test_label_tensor) 
test_loader = DataLoader(test_dataset, batch_size=batch_size) 

In [24]:
model = GRU_AT(num_classes).to(device)

In [25]:
# Loss and optimizer
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate, weight_decay=1e-3) 
#optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate) 
milestones = [50,100,150,200,250]
milestones = [a * len(train_loader) for a in milestones]
scheduler = MultiStepLR(optimizer, milestones=milestones, gamma=0.5)

In [26]:
# Train the model
total_step = len(train_loader)
for epoch in range(num_epochs):
    correct=0
    total=0
    running_loss = 0
    for i, (X, Y) in enumerate(train_loader):
        X = X.to(device)
        Y = Y.to(device)
        
        
        # Forward pass
        outputs = model(X)
        loss = criterion(outputs, Y)
        
        # Backward and optimize
        optimizer.zero_grad()
        loss.backward()
        #scheduler.step() 
        #print(scheduler.get_last_lr()[0])
      
        optimizer.step()
        scheduler.step() 
        #print(optimizer.param_groups[0]["lr"])
        
        _, predicted = outputs.max(1)
        total += Y.size(0)
        correct += predicted.eq(Y).sum().item()
        running_loss += loss.item()
        accu=100.*correct/total
        train_loss = running_loss/(i+1)
        print ('Epoch [{}/{}], Step [{}/{}], Training Accuracy: {:.4f}%, Training Loss: {:.4f}%'.format(epoch+1, num_epochs, i+1, total_step, accu, train_loss))
    
   
        #writer.add_scalar(f'train/accuracy', accu, epoch)
        #writer.add_scalar(f'train/loss', train_loss, epoch)
        writer.add_scalars(f'train/accuracy_loss', {
            'accuracy': accu,
            'loss': train_loss,
        }, epoch)
        

Epoch [1/300], Step [1/225], Training Accuracy: 28.1250%, Training Loss: 1.4337%
Epoch [1/300], Step [2/225], Training Accuracy: 22.6562%, Training Loss: 1.5229%
Epoch [1/300], Step [3/225], Training Accuracy: 21.3542%, Training Loss: 1.5350%
Epoch [1/300], Step [4/225], Training Accuracy: 22.2656%, Training Loss: 1.5105%
Epoch [1/300], Step [5/225], Training Accuracy: 23.7500%, Training Loss: 1.4944%
Epoch [1/300], Step [6/225], Training Accuracy: 23.4375%, Training Loss: 1.5057%
Epoch [1/300], Step [7/225], Training Accuracy: 24.3304%, Training Loss: 1.4905%
Epoch [1/300], Step [8/225], Training Accuracy: 24.0234%, Training Loss: 1.4934%
Epoch [1/300], Step [9/225], Training Accuracy: 25.0000%, Training Loss: 1.4942%
Epoch [1/300], Step [10/225], Training Accuracy: 25.3125%, Training Loss: 1.4874%
Epoch [1/300], Step [11/225], Training Accuracy: 25.0000%, Training Loss: 1.4900%
Epoch [1/300], Step [12/225], Training Accuracy: 25.3906%, Training Loss: 1.4801%
Epoch [1/300], Step [13/2

Epoch [1/300], Step [111/225], Training Accuracy: 29.2089%, Training Loss: 1.3986%
Epoch [1/300], Step [112/225], Training Accuracy: 29.2550%, Training Loss: 1.3978%
Epoch [1/300], Step [113/225], Training Accuracy: 29.3003%, Training Loss: 1.3978%
Epoch [1/300], Step [114/225], Training Accuracy: 29.3586%, Training Loss: 1.3964%
Epoch [1/300], Step [115/225], Training Accuracy: 29.2935%, Training Loss: 1.3962%
Epoch [1/300], Step [116/225], Training Accuracy: 29.3238%, Training Loss: 1.3956%
Epoch [1/300], Step [117/225], Training Accuracy: 29.3269%, Training Loss: 1.3954%
Epoch [1/300], Step [118/225], Training Accuracy: 29.3035%, Training Loss: 1.3955%
Epoch [1/300], Step [119/225], Training Accuracy: 29.2805%, Training Loss: 1.3953%
Epoch [1/300], Step [120/225], Training Accuracy: 29.2969%, Training Loss: 1.3951%
Epoch [1/300], Step [121/225], Training Accuracy: 29.3259%, Training Loss: 1.3948%
Epoch [1/300], Step [122/225], Training Accuracy: 29.3673%, Training Loss: 1.3942%
Epoc

Epoch [1/300], Step [224/225], Training Accuracy: 31.5081%, Training Loss: 1.3625%
Epoch [1/300], Step [225/225], Training Accuracy: 31.4967%, Training Loss: 1.3628%
Epoch [2/300], Step [1/225], Training Accuracy: 34.3750%, Training Loss: 1.3214%
Epoch [2/300], Step [2/225], Training Accuracy: 32.8125%, Training Loss: 1.3495%
Epoch [2/300], Step [3/225], Training Accuracy: 30.2083%, Training Loss: 1.3584%
Epoch [2/300], Step [4/225], Training Accuracy: 31.2500%, Training Loss: 1.3359%
Epoch [2/300], Step [5/225], Training Accuracy: 31.8750%, Training Loss: 1.3294%
Epoch [2/300], Step [6/225], Training Accuracy: 32.0312%, Training Loss: 1.3361%
Epoch [2/300], Step [7/225], Training Accuracy: 32.3661%, Training Loss: 1.3341%
Epoch [2/300], Step [8/225], Training Accuracy: 31.8359%, Training Loss: 1.3293%
Epoch [2/300], Step [9/225], Training Accuracy: 31.7708%, Training Loss: 1.3329%
Epoch [2/300], Step [10/225], Training Accuracy: 32.8125%, Training Loss: 1.3253%
Epoch [2/300], Step [11

Epoch [2/300], Step [113/225], Training Accuracy: 36.0066%, Training Loss: 1.3020%
Epoch [2/300], Step [114/225], Training Accuracy: 36.0334%, Training Loss: 1.3009%
Epoch [2/300], Step [115/225], Training Accuracy: 36.0462%, Training Loss: 1.3008%
Epoch [2/300], Step [116/225], Training Accuracy: 36.0587%, Training Loss: 1.3007%
Epoch [2/300], Step [117/225], Training Accuracy: 36.0310%, Training Loss: 1.3014%
Epoch [2/300], Step [118/225], Training Accuracy: 36.0169%, Training Loss: 1.3013%
Epoch [2/300], Step [119/225], Training Accuracy: 35.9900%, Training Loss: 1.3012%
Epoch [2/300], Step [120/225], Training Accuracy: 36.0547%, Training Loss: 1.3009%
Epoch [2/300], Step [121/225], Training Accuracy: 36.0795%, Training Loss: 1.3007%
Epoch [2/300], Step [122/225], Training Accuracy: 36.0656%, Training Loss: 1.3003%
Epoch [2/300], Step [123/225], Training Accuracy: 36.0772%, Training Loss: 1.3003%
Epoch [2/300], Step [124/225], Training Accuracy: 36.1139%, Training Loss: 1.3007%
Epoc

Epoch [3/300], Step [1/225], Training Accuracy: 45.3125%, Training Loss: 1.2023%
Epoch [3/300], Step [2/225], Training Accuracy: 39.0625%, Training Loss: 1.2767%
Epoch [3/300], Step [3/225], Training Accuracy: 34.3750%, Training Loss: 1.3189%
Epoch [3/300], Step [4/225], Training Accuracy: 34.7656%, Training Loss: 1.3071%
Epoch [3/300], Step [5/225], Training Accuracy: 36.2500%, Training Loss: 1.2927%
Epoch [3/300], Step [6/225], Training Accuracy: 35.9375%, Training Loss: 1.2941%
Epoch [3/300], Step [7/225], Training Accuracy: 36.1607%, Training Loss: 1.2907%
Epoch [3/300], Step [8/225], Training Accuracy: 36.9141%, Training Loss: 1.2873%
Epoch [3/300], Step [9/225], Training Accuracy: 37.1528%, Training Loss: 1.2832%
Epoch [3/300], Step [10/225], Training Accuracy: 37.6562%, Training Loss: 1.2728%
Epoch [3/300], Step [11/225], Training Accuracy: 37.6420%, Training Loss: 1.2712%
Epoch [3/300], Step [12/225], Training Accuracy: 37.7604%, Training Loss: 1.2698%
Epoch [3/300], Step [13/2

...

Epoch [298/300], Step [121/225], Training Accuracy: 99.6126%, Training Loss: 0.0221%
Epoch [298/300], Step [122/225], Training Accuracy: 99.6158%, Training Loss: 0.0221%
Epoch [298/300], Step [123/225], Training Accuracy: 99.6189%, Training Loss: 0.0219%
Epoch [298/300], Step [124/225], Training Accuracy: 99.6220%, Training Loss: 0.0218%
Epoch [298/300], Step [125/225], Training Accuracy: 99.6250%, Training Loss: 0.0217%
Epoch [298/300], Step [126/225], Training Accuracy: 99.6280%, Training Loss: 0.0216%
Epoch [298/300], Step [127/225], Training Accuracy: 99.6309%, Training Loss: 0.0217%
Epoch [298/300], Step [128/225], Training Accuracy: 99.6338%, Training Loss: 0.0218%
Epoch [298/300], Step [129/225], Training Accuracy: 99.6124%, Training Loss: 0.0219%
Epoch [298/300], Step [130/225], Training Accuracy: 99.6154%, Training Loss: 0.0219%
Epoch [298/300], Step [131/225], Training Accuracy: 99.6183%, Training Loss: 0.0218%
Epoch [298/300], Step [132/225], Training Accuracy: 99.6212%, Tra

Epoch [299/300], Step [10/225], Training Accuracy: 99.8438%, Training Loss: 0.0166%
Epoch [299/300], Step [11/225], Training Accuracy: 99.8580%, Training Loss: 0.0171%
Epoch [299/300], Step [12/225], Training Accuracy: 99.7396%, Training Loss: 0.0175%
Epoch [299/300], Step [13/225], Training Accuracy: 99.6394%, Training Loss: 0.0180%
Epoch [299/300], Step [14/225], Training Accuracy: 99.6652%, Training Loss: 0.0172%
Epoch [299/300], Step [15/225], Training Accuracy: 99.6875%, Training Loss: 0.0174%
Epoch [299/300], Step [16/225], Training Accuracy: 99.6094%, Training Loss: 0.0177%
Epoch [299/300], Step [17/225], Training Accuracy: 99.6324%, Training Loss: 0.0175%
Epoch [299/300], Step [18/225], Training Accuracy: 99.5660%, Training Loss: 0.0194%
Epoch [299/300], Step [19/225], Training Accuracy: 99.5888%, Training Loss: 0.0192%
Epoch [299/300], Step [20/225], Training Accuracy: 99.6094%, Training Loss: 0.0191%
Epoch [299/300], Step [21/225], Training Accuracy: 99.5536%, Training Loss: 

Epoch [299/300], Step [126/225], Training Accuracy: 99.6032%, Training Loss: 0.0216%
Epoch [299/300], Step [127/225], Training Accuracy: 99.6063%, Training Loss: 0.0217%
Epoch [299/300], Step [128/225], Training Accuracy: 99.5850%, Training Loss: 0.0221%
Epoch [299/300], Step [129/225], Training Accuracy: 99.5761%, Training Loss: 0.0221%
Epoch [299/300], Step [130/225], Training Accuracy: 99.5553%, Training Loss: 0.0223%
Epoch [299/300], Step [131/225], Training Accuracy: 99.5587%, Training Loss: 0.0222%
Epoch [299/300], Step [132/225], Training Accuracy: 99.5620%, Training Loss: 0.0222%
Epoch [299/300], Step [133/225], Training Accuracy: 99.5653%, Training Loss: 0.0222%
Epoch [299/300], Step [134/225], Training Accuracy: 99.5686%, Training Loss: 0.0220%
Epoch [299/300], Step [135/225], Training Accuracy: 99.5718%, Training Loss: 0.0220%
Epoch [299/300], Step [136/225], Training Accuracy: 99.5749%, Training Loss: 0.0220%
Epoch [299/300], Step [137/225], Training Accuracy: 99.5780%, Tra

Epoch [300/300], Step [15/225], Training Accuracy: 99.3750%, Training Loss: 0.0253%
Epoch [300/300], Step [16/225], Training Accuracy: 99.4141%, Training Loss: 0.0250%
Epoch [300/300], Step [17/225], Training Accuracy: 99.4485%, Training Loss: 0.0246%
Epoch [300/300], Step [18/225], Training Accuracy: 99.4792%, Training Loss: 0.0244%
Epoch [300/300], Step [19/225], Training Accuracy: 99.5066%, Training Loss: 0.0234%
Epoch [300/300], Step [20/225], Training Accuracy: 99.5312%, Training Loss: 0.0227%
Epoch [300/300], Step [21/225], Training Accuracy: 99.5536%, Training Loss: 0.0224%
Epoch [300/300], Step [22/225], Training Accuracy: 99.5739%, Training Loss: 0.0221%
Epoch [300/300], Step [23/225], Training Accuracy: 99.5924%, Training Loss: 0.0220%
Epoch [300/300], Step [24/225], Training Accuracy: 99.6094%, Training Loss: 0.0216%
Epoch [300/300], Step [25/225], Training Accuracy: 99.6250%, Training Loss: 0.0215%
Epoch [300/300], Step [26/225], Training Accuracy: 99.6394%, Training Loss: 

Epoch [300/300], Step [130/225], Training Accuracy: 99.4111%, Training Loss: 0.0242%
Epoch [300/300], Step [131/225], Training Accuracy: 99.4036%, Training Loss: 0.0242%
Epoch [300/300], Step [132/225], Training Accuracy: 99.4081%, Training Loss: 0.0241%
Epoch [300/300], Step [133/225], Training Accuracy: 99.4126%, Training Loss: 0.0241%
Epoch [300/300], Step [134/225], Training Accuracy: 99.4170%, Training Loss: 0.0240%
Epoch [300/300], Step [135/225], Training Accuracy: 99.4213%, Training Loss: 0.0239%
Epoch [300/300], Step [136/225], Training Accuracy: 99.4256%, Training Loss: 0.0238%
Epoch [300/300], Step [137/225], Training Accuracy: 99.4297%, Training Loss: 0.0237%
Epoch [300/300], Step [138/225], Training Accuracy: 99.4339%, Training Loss: 0.0237%
Epoch [300/300], Step [139/225], Training Accuracy: 99.4267%, Training Loss: 0.0237%
Epoch [300/300], Step [140/225], Training Accuracy: 99.4308%, Training Loss: 0.0239%
Epoch [300/300], Step [141/225], Training Accuracy: 99.4348%, Tra

In [27]:
from playsound import playsound
playsound(u"sound.mp3")

In [28]:
# Test the model
model.eval()  # eval mode (batchnorm uses moving mean/variance instead of mini-batch mean/variance)
with torch.no_grad():
    correct = 0
    total = 0
    for X, Y in test_loader:
        X = X.to(device)
        Y = Y.to(device)
        outputs = model(X)
        _, predicted = torch.max(outputs.data, 1)
        total += Y.size(0)
        correct += (predicted == Y).sum().item()

    print('Test Accuracy : {} %'.format(100 * correct / total))

# Save the model checkpoint
#torch.save(model.state_dict(), 'model.ckpt')

Test Accuracy : 43.66314619232907 %
